In [1]:
import pandas as pd
import random

# Charger les données à partir des fichiers Excel
train_data = pd.read_excel('train.xlsx')
test_data = pd.read_excel('test.xlsx')

# Créer des paires de tweets de manière aléatoire
def create_random_tweet_pairs(data, num_pairs):
    tweet_pairs = []
    same_user_pairs = []
    different_user_pairs = []
    
    # Séparer les tweets par utilisateur
    user_tweets = {}
    for index, row in data.iterrows():
        user = row['user']
        tweet = row['text']
        if user not in user_tweets:
            user_tweets[user] = []
        user_tweets[user].append(tweet)
    
    # Créer des paires de tweets
    for _ in range(num_pairs):
        # Choix aléatoire d'un utilisateur
        user1, user2 = random.sample(list(user_tweets.keys()), 2)
        # Choix aléatoire d'un tweet pour chaque utilisateur
        tweet1 = random.choice(user_tweets[user1])
        tweet2 = random.choice(user_tweets[user2])
        
        tweet_pairs.append((tweet1, tweet2))
        
        # Vérifier si les tweets proviennent du même utilisateur ou non
        if user1 == user2:
            same_user_pairs.append((tweet1, tweet2, 1))  # 1 pour les paires du même utilisateur
        else:
            different_user_pairs.append((tweet1, tweet2, 0))  # 0 pour les paires de différents utilisateurs
    
    # Mélanger les paires pour obtenir un ordre aléatoire
    random.shuffle(same_user_pairs)
    random.shuffle(different_user_pairs)
    
    # Concaténer les paires pour obtenir un ensemble de paires équilibré
    balanced_pairs = same_user_pairs[:num_pairs//2] + different_user_pairs[:num_pairs//2]
    random.shuffle(balanced_pairs)
    
    return balanced_pairs

# Créer des paires de tweets pour les données d'entraînement et de test
train_tweet_pairs = create_random_tweet_pairs(train_data, num_pairs=1000)
test_tweet_pairs = create_random_tweet_pairs(test_data, num_pairs=500)

# Afficher un exemple de paire de tweets
print("Exemple de paire de tweets pour les données d'entraînement:")
print(train_tweet_pairs[0])
# Étiqueter les paires de tweets en fonction de la similarité des utilisateurs
def label_tweet_pairs(tweet_pairs, data):
    labeled_pairs = []
    for pair in tweet_pairs:
        tweet1, tweet2, _ = pair  # Ignorer l'étiquette de similarité
        user1 = data[data['text'] == tweet1]['user'].iloc[0]
        user2 = data[data['text'] == tweet2]['user'].iloc[0]
        similarity_label = 1 if user1 == user2 else 0
        labeled_pairs.append((tweet1, tweet2, similarity_label))
    return labeled_pairs



# Créer des paires de tweets pour les données d'entraînement et de test
train_tweet_pairs = create_random_tweet_pairs(train_data, num_pairs=1000)
test_tweet_pairs = create_random_tweet_pairs(test_data, num_pairs=500)

# Étiqueter les paires de tweets pour les données d'entraînement et de test
labeled_train_pairs = label_tweet_pairs(train_tweet_pairs, train_data)
labeled_test_pairs = label_tweet_pairs(test_tweet_pairs, test_data)


# Afficher un exemple de paire de tweets étiquetée
print("Exemple de paire de tweets étiquetée pour les données d'entraînement:")
print(labeled_train_pairs[0])

Exemple de paire de tweets pour les données d'entraînement:
('@todddln bring your full body outfits!', 'This music video was made on a Commodore 64 with less data than it takes to send this tweet. https://goo.gl/pnmrA9\xa0pic.twitter.com/XQrKvESuSo', 0)
Exemple de paire de tweets étiquetée pour les données d'entraînement:
('Philadelphia right nowpic.twitter.com/0Qxaz9qcuM', '#SummerGoalspic.twitter.com/LncRrqQplN', 0)


In [2]:
import string
import re
import nltk
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
from nltk.stem import PorterStemmer, WordNetLemmatizer

def clean_text(tweet):
    print("Tweet avant nettoyage :", tweet[:50])  # Afficher seulement les 100 premiers caractères
    # Convertir en minuscules
    tweet = tweet.lower()
    # Supprimer la ponctuation
    tweet = tweet.translate(str.maketrans('', '', string.punctuation))
    # Tokenisation
    tokens = word_tokenize(tweet)
    # Supprimer les mots vides
    stop_words = set(stopwords.words('english'))
    tokens = [word for word in tokens if word not in stop_words]
    # Lemmatisation ou racinisation (stemming)
    lemmatizer = WordNetLemmatizer()
    tokens = [lemmatizer.lemmatize(word) for word in tokens]
    # Rejoindre les mots en une seule chaîne
    cleaned_tweet = ' '.join(tokens)
    print("Tweet après nettoyage :", cleaned_tweet[:50])  # Afficher seulement les 100 premiers caractères
    return cleaned_tweet

def create_random_tweet_pairs(data, num_pairs):
    tweet_pairs = []
    same_user_pairs = []
    different_user_pairs = []
    
    user_tweets = {}
    for index, row in data.iterrows():
        user = row['user']
        tweet = row['text']
        if user not in user_tweets:
            user_tweets[user] = []
        # Nettoyage du texte
        cleaned_tweet = clean_text(tweet)
        user_tweets[user].append(cleaned_tweet)
    
       # Créer des paires de tweets
    for _ in range(num_pairs):
        # Choix aléatoire d'un utilisateur
        user1, user2 = random.sample(list(user_tweets.keys()), 2)
        # Choix aléatoire d'un tweet pour chaque utilisateur
        tweet1 = random.choice(user_tweets[user1])
        tweet2 = random.choice(user_tweets[user2])
        
        tweet_pairs.append((tweet1, tweet2))
        
        # Vérifier si les tweets proviennent du même utilisateur ou non
        if user1 == user2:
            same_user_pairs.append((tweet1, tweet2, 1))  # 1 pour les paires du même utilisateur
        else:
            different_user_pairs.append((tweet1, tweet2, 0))  # 0 pour les paires de différents utilisateurs
    
    # Mélanger les paires pour obtenir un ordre aléatoire
    random.shuffle(same_user_pairs)
    random.shuffle(different_user_pairs)

# Concaténer les paires pour obtenir un ensemble de paires équilibré
    balanced_pairs = same_user_pairs[:num_pairs//2] + different_user_pairs[:num_pairs//2]
    random.shuffle(balanced_pairs)
    
    return balanced_pairs

# Créer des paires de tweets pour les données d'entraînement et de test
train_tweet_pairs = create_random_tweet_pairs(train_data, num_pairs=1000)
test_tweet_pairs = create_random_tweet_pairs(test_data, num_pairs=500)

def label_tweet_pairs(tweet_pairs, data):
    labeled_pairs = []
    for pair in tweet_pairs:
        tweet1, tweet2, _ = pair
        user1 = data[data['text'] == tweet1]['user'].iloc[0]
        user2 = data[data['text'] == tweet2]['user'].iloc[0]
        similarity_label = 1 if user1 == user2 else 0
        # Nettoyage du texte
        cleaned_tweet1 = clean_text(tweet1)
        cleaned_tweet2 = clean_text(tweet2)
        labeled_pairs.append((cleaned_tweet1, cleaned_tweet2, similarity_label))
    return labeled_pairs

Tweet avant nettoyage : Make your reservation now. #GagaAHSHotelhttps://am
Tweet après nettoyage : make reservation gagaahshotelhttpsamptwimgcomvbe65
Tweet avant nettoyage : @DrunkyViviana we shot for 3 days but planned for 
Tweet après nettoyage : drunkyviviana shot 3 day planned week
Tweet avant nettoyage :  me I'm back in the NY GROOVEpic.twitter.com/ckF0l
Tweet après nettoyage : im back ny groovepictwittercomckf0lsudt5
Tweet avant nettoyage : GLEE WAS SO AMAZING! AH!!!!
Tweet après nettoyage : glee amazing ah
Tweet avant nettoyage : LIVE with @JoJoWright in 5 minutes on @1027KIISFM
Tweet après nettoyage : live jojowright 5 minute 1027kiisfm
Tweet avant nettoyage : Check this out! #littlemonsters on Place. Diana in
Tweet après nettoyage : check littlemonsters place diana monsterstyle http
Tweet avant nettoyage : such a cool video!!! I love my fans so much thank 
Tweet après nettoyage : cool video love fan much thank celebrating spirit 
Tweet avant nettoyage : do you now how hard it 

In [3]:
import torch
from transformers import BertTokenizer, BertModel

# Charger le tokenizer et le modèle BERT
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
model = BertModel.from_pretrained('bert-base-uncased')

def encode_tweets(tweet_pairs):
    encoded_pairs = []
    for tweet1, tweet2, label in tweet_pairs:
        # Tokenisation et encodage des tweets
        inputs = tokenizer(tweet1, tweet2, return_tensors='pt', padding=True, truncation=True)
        # Passer les inputs à travers le modèle BERT
        with torch.no_grad():
            outputs = model(**inputs)
        # Récupérer la représentation vectorielle du premier tweet
        embeddings_tweet1 = outputs.last_hidden_state.mean(dim=1).squeeze(0)
        # Récupérer la représentation vectorielle du deuxième tweet
        embeddings_tweet2 = outputs.last_hidden_state.mean(dim=1).squeeze(0)  # Répéter le seul vecteur d'embeddings
        # Ajouter les embeddings et l'étiquette au tuple
        encoded_pairs.append((embeddings_tweet1, embeddings_tweet2, label))
    return encoded_pairs



# Encodage des paires de tweets
encoded_train_pairs = encode_tweets(train_tweet_pairs)
encoded_test_pairs = encode_tweets(test_tweet_pairs)

# Afficher les premières paires encodées pour vérification
print("Première paire encodée pour les données d'entraînement :", encoded_train_pairs[0])
print("Première paire encodée pour les données de test :", encoded_test_pairs[0])

# Convertir les représentations vectorielles en tenseurs PyTorch
train_data_tensors = [(torch.tensor(tweet1), torch.tensor(tweet2), torch.tensor(label)) for tweet1, tweet2, label in encoded_train_pairs]
test_data_tensors = [(torch.tensor(tweet1), torch.tensor(tweet2), torch.tensor(label)) for tweet1, tweet2, label in encoded_test_pairs]

# Afficher les premiers tenseurs pour vérification
print("Premier tensor pour les données d'entraînement :", train_data_tensors[0])
print("Premier tensor pour les données de test :", test_data_tensors[0])


import torch
import torch.nn as nn
import torch.optim as optim
from sklearn.metrics import precision_score, recall_score, f1_score

# Définir la classe du modèle
class SimilarityModel(nn.Module):
    def __init__(self, input_dim):
        super(SimilarityModel, self).__init__()
        self.dense = nn.Linear(input_dim, 1)
        self.sigmoid = nn.Sigmoid()
    
    def forward(self, x):
        x = self.dense(x)
        x = self.sigmoid(x)
        return x

# Créer une instance du modèle en utilisant la dimension appropriée
model = SimilarityModel(input_dim=1)  # Utiliser une dimension d'entrée de 1 car la distance de Manhattan est un scalaire

# Définir la fonction de perte et l'optimiseur
criterion = nn.BCELoss()
optimizer = optim.Adam(model.parameters(), lr=0.001)

# Entraînement du modèle
num_epochs = 10
for epoch in range(num_epochs):
    for tweet1, tweet2, label in encoded_train_pairs:
        # Calculer la représentation du tweet en utilisant la distance de Manhattan
        manhattan_distance = torch.abs(tweet1 - tweet2).sum()  # Calcul de la distance de Manhattan
        
        # Passer la distance de Manhattan à travers la couche dense
        output = model(manhattan_distance.unsqueeze(0))  # Ajouter une dimension supplémentaire
        
        # Calculer la perte
        loss = criterion(output, torch.tensor([label], dtype=torch.float))
        
        # Rétropropagation et mise à jour des poids
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()

# Évaluation du modèle
true_labels = []
predicted_labels = []
with torch.no_grad():
    for tweet1, tweet2, label in encoded_test_pairs:
        # Calculer la représentation du tweet en utilisant la distance de Manhattan
        manhattan_distance = torch.abs(tweet1 - tweet2).sum()  # Calcul de la distance de Manhattan
        
        # Passer la distance de Manhattan à travers le modèle
        output = model(manhattan_distance.unsqueeze(0))
        
        # Convertir la sortie en prédiction binaire
        predicted_label = 1 if output.item() > 0.5 else 0
        
        true_labels.append(label)
        predicted_labels.append(predicted_label)

# Calculer les métriques d'évaluation
precision = precision_score(true_labels, predicted_labels)
recall = recall_score(true_labels, predicted_labels)
f1 = f1_score(true_labels, predicted_labels)

print("Precision:", precision)
print("Recall:", recall)
print("F1 Score:", f1)


C:\Users\pc\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


Première paire encodée pour les données d'entraînement : (tensor([-3.4798e-02,  9.2111e-02,  5.1225e-01, -7.4737e-02,  2.7235e-01,
         3.0721e-02,  1.1263e-01,  1.6914e-01, -1.0336e-01, -2.7536e-01,
        -1.2816e-01,  1.1459e-02,  1.1710e-02,  2.9140e-01,  3.3257e-02,
         3.5068e-01, -6.8345e-02,  2.1988e-01, -9.6825e-02,  9.7088e-04,
         3.9196e-01,  1.4874e-02,  2.4042e-01,  1.5546e-01,  5.6027e-02,
        -1.2182e-01,  1.5963e-01, -1.3225e-02, -1.7364e-01,  5.1078e-02,
         4.4210e-02, -2.6938e-01,  9.8575e-02, -1.5721e-01, -7.9600e-02,
        -2.9738e-02, -6.7895e-02,  1.7044e-01,  1.7943e-01,  1.9409e-01,
        -2.8775e-02, -3.7775e-01, -2.7663e-02,  2.2777e-02, -3.6233e-01,
        -2.6419e-01, -2.7572e-01,  2.9514e-01,  2.6638e-01, -1.5759e-02,
        -1.3465e-01,  3.8271e-01,  1.5689e-01,  3.7618e-02, -2.6751e-02,
         4.2942e-01,  1.2299e-01, -2.6862e-01, -6.6176e-02, -1.8094e-01,
        -4.9673e-02, -1.8932e-01,  1.2525e-01,  1.1655e-01,  6.984

C:\Users\pc\AppData\Local\Temp\ipykernel_20608\2847710539.py:35: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  train_data_tensors = [(torch.tensor(tweet1), torch.tensor(tweet2), torch.tensor(label)) for tweet1, tweet2, label in encoded_train_pairs]
C:\Users\pc\AppData\Local\Temp\ipykernel_20608\2847710539.py:36: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  test_data_tensors = [(torch.tensor(tweet1), torch.tensor(tweet2), torch.tensor(label)) for tweet1, tweet2, label in encoded_test_pairs]


Precision: 0.0
Recall: 0.0
F1 Score: 0.0


C:\Users\pc\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\sklearn\metrics\_classification.py:1471: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\pc\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\sklearn\metrics\_classification.py:1471: UndefinedMetricWarning: Recall is ill-defined and being set to 0.0 due to no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\pc\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\sklearn\metrics\_classification.py:1760: UndefinedMetricWarning: F-score is ill-defined and being 